# CSTR - Output Feedback GP-MPC
In this example MPC is used to control the concentration of a product in a continuous stirred-tank reactor (CSTR). We will see how to

1. Train a Gaussian Process Regressor (GP)
2. Use the GP to build a black-box input-output model
3. Setup a Nonlinear Model Predictive Control Problem

This example is a simplified version of the simulations in [Maiworm, Limon, Manzano, Findeisen (2018)] and [Maiworm, Limon, Findeisen (2021)].

#### Import necessary libraries

In [1]:
import numpy as np

from hilo_mpc import NMPC, SimpleControlLoop, GP, SquaredExponentialKernel, Model, set_plot_backend
from hilo_mpc.library import cstr_seborg

## Process / Plant Model
In a continuous stirred-tank reactor (CSTR, _Seborg et al. (1989)_) a substrate $A$ is converted into product $B$. The reaction of substrate $A$ can be described by the following set of differential equations

$$
\begin{align}
  \dot C_A(t) &= \frac{q_0}{V} \big( C_{A \text f} - C_A(t) \big) - k_0 \exp \left( \frac{-E}{R T(t)} \right) C_A(t) \\
  \dot T(t) &= \frac{q_0}{V} \big( T_\text f - T(t) \big) - \frac{\Delta H_\text r k_0}{\rho C_\text p}
               \exp\left( \frac{-E}{R T(t)} \right) C_A(t) + \frac{U A}{V \rho C_p} \big( T_\text c(t) - T(t) \big) \\
  \dot T_\text c(t) &= \frac{T_\text c(t) - T_\text{cr}(t)}{\tau} \ ,
\end{align}
$$

where the coolant temperature reference $T_\text{cr}$ (K) is the input to the reactor and the concentration $C_A$ (mol/l) the output, i.e., $u = T_\text{cr}$ and $y = C_A$. 
The tank and coolant temperature are $T$ and $T_\text c$. All other variables are constant parameters.
Inputs and outputs are restricted to lie in constraint compact sets, i.e., $u \in \mathcal U \subseteq \mathbb R$ and $y \in \mathcal Y \subseteq \mathbb R$, where $\mathcal U$ are hard constraints and $\mathcal Y$ can be hard or soft constraints.

In [2]:
# Equilibria
x0_plant = [0.6205, 348, 347.5] # initial point
y0 = x0_plant[0] 
u0 = x0_plant[2]
x_ref = [0.4674, 355.9, 356]
y_ref = x_ref[0]
u_ref = x_ref[2]

# Constraints
y_lb = 0.35
y_ub = 0.65
u_lb = 335
u_ub = 372

# Simulation parameters
Ts = 0.5           # sampling time (min)
T = 25             # simulation time (min)
N_step = int(T/Ts) # simulation time steps

# Plant Parameters
CAf = 1 # mol/l
Cp = 0.3  # J/(g*K)
DeltaHr = 10000  # J/mol
ER = 9750  # K
k0 = 6e10  # 1/min
q0 = 10  # l/min
rho = 1100  # g/l
tau = 1.5  # min
UA = 70000  # J/(min*K)
V = 150  # l
Tf = 370  # K

# Set up plant
plant = Model(plot_backend='bokeh', name='Plant', discrete=True)

# Set states and inputs
x = plant.set_dynamical_states(['C_A', 'T', 'T_c'])
u = plant.set_inputs(['T_cr'])

# Unwrap states
C_A = x[0]
T   = x[1]
T_c = x[2]

# Unwrap inputs
T_cr = u[0]

# Dynamics (discrete, forward Euler)
tmp = k0 * np.exp(-ER/T) * C_A

C_A_next = C_A + Ts * ( q0/V * (CAf - C_A) - tmp )
T_next   = T + Ts *( q0/V * (Tf - T) - DeltaHr/(rho*Cp) * tmp + UA/(V*rho*Cp) * (T_c - T) )
T_c_next = T_c + Ts * ((T_cr - T_c) / tau)

# Set difference equations
plant.set_dynamical_equations([C_A_next, T_next, T_c_next])

# Initilaize model
plant.setup(dt=Ts)

# Initial condition
plant.set_initial_conditions(x0=x0_plant)

C:\Users\Bruno\Documents\python_packages\examples\lib\site-packages\hilo_mpc\modules\dynamic_model\dynamic_model.py:2939: UserWarning: The model was initialized as a discrete model, but no sampling time was implemented in the model. Assuming that the sampling time 'dt' is already integrated numerically.
  warnings.warn("The model was initialized as a discrete model, but no sampling time was implemented in "


# MPC with true dynamics
The considered control objective is set-point stabilization and optimal set-point change, i.e., we want to steer the system from an initial point $(y_0,u_0) = \big(0.6205 \, \text{(mol/l)}, 347.5 \, \text{(K)} \big)$ to a target reference point $(y_\text{ref},u_\text{ref}) = \big(0.4674 \, \text{(mol/l)}, 356 \, \text{(K)} \big)$, while satisfying the constraints and stabilizing the system at the target. 
To this end, we employ model predictive control and start with a MPC controller that uses the real plant model as prediction model.

The MPC formulation is
$$
\begin{align}
        \min_{\mathbf{u}_k} \ & \sum_{i=0}^{N-1} \ell \big( x_{k+i|k}, u_{k+i|k}\big) + V_f \big( x_{k+N|k} - x_\text{ref} \big) \ , \\
        \text{s.t.} \quad &\forall i \in \mathcal I_{0:N-1}\!: \\
        & x_{k+i+1|k} = f_{\rm plant}(x_{k+i|k},\,u_{k+i|k}),\quad x_{k|k}=x_k\\
        & u_{k+i|k} \in \mathcal U \\ 
        & x_{k+i|k} \in \mathcal X
\end{align}
$$
with the to be optimized input sequence $\mathbf{u}_k = \{u_{k|k}, u_{k+1|k}, \ldots, u_{k+N-1|k}\}$, the prediction horizon $N$, the initial state $x_k$ and the constrained set $\mathcal X \in \mathbb R^3$.




In [3]:
nmpc = NMPC(plant)

# Set horizon
nmpc.horizon = 5

# Set cost function ------------------------------
# ...with scaling
# nmpc.set_scaling(x_scaling=[0.5, 350, 350], u_scaling=[350])
# nmpc.quad_stage_cost.add_states(names=['C_A'], weights=[100], trajectory_tracking=True)
# nmpc.quad_stage_cost.add_inputs(names=['T_cr'], weights=[100], trajectory_tracking=True)
# nmpc.quad_terminal_cost.add_states(names=['C_A'], weights=[100], trajectory_tracking=True)

# ...without scaling
nmpc.quad_stage_cost.add_states(names=['C_A'], weights=[100], trajectory_tracking=True)
nmpc.quad_stage_cost.add_inputs(names=['T_cr'], weights=[0.0002], trajectory_tracking=True)
nmpc.quad_terminal_cost.add_states(names=['C_A'], weights=[100], trajectory_tracking=True)
# -------------------------------------------------

# Set constraints
nmpc.set_box_constraints(x_lb=[y_lb, 0, 0], x_ub=[y_ub, 500, 500], u_lb=u_lb, u_ub=u_ub)

# Initial guess
nmpc.set_initial_guess(x_guess=x0_plant, u_guess=u0)

# Set up controller
nmpc.setup(options={'print_level': 0, 
                    'objective_function':'discrete', 
                    'integration_method': 'discrete'})

# Reference trajectory
ref_trajectory = np.zeros([2,N_step + nmpc.horizon + 1])
ref_trajectory[0,:10] = y0
ref_trajectory[0,10:] = y_ref
ref_trajectory[1,:10] = u0
ref_trajectory[1,10:] = u_ref
ref_trajectory_y = ref_trajectory[0, :]
ref_trajectory_u = ref_trajectory[1, :]

# Run the simulation
scl = SimpleControlLoop(plant, nmpc)
scl.run(N_step, p=plant.solution.get_by_id('p:0'), ref_sc={'T_cr': ref_trajectory_u, 'C_A': ref_trajectory_y},
        ref_tc={'C_A': ref_trajectory_y})

# Plots
scl.plot(
    ('t', 'T_cr'),
    ('t', 'C_A'),
    title=('input', 'output'),
    figsize=(900, 300),
    layout=(2, 1),
    background_fill_color='#fafafa',
    output_file='gp_nmpc_cstr_output_feedbacknominal_controller.html',
    output_notebook=True
)

C:\Users\Bruno\Documents\python_packages\examples\lib\site-packages\hilo_mpc\modules\base.py:2174: UserWarning: Plots are disabled, since no backend was selected.
  warnings.warn("Plots are disabled, since no backend was selected.")



******************************************************************************
This program contains Ipopt, a library for large-scale nonlinear optimization.
 Ipopt is released as open source code under the Eclipse Public License (EPL).
         For more information visit http://projects.coin-or.org/Ipopt
******************************************************************************



Loading BokehJS ...

'gp_nmpc_cstr_output_feedbacknominal_controller.html'

# MPC with GP model
The considered control objective is the same as above but now we the detailed physical plant model is not available.
Instead, we obtain only noisy output measurements that are used to learn an input-output model in the form of a discrete-time nonlinear autoregressive model with exogeneous input (NARX).
The model takes the form
$$
\begin{align}
  \hat y_{k+1} = f(x_k,u_k) \ ,
\end{align} 
$$
where the hat notation $\hat{\cdot}$ denotes an estimated quantity, $k$ denotes the discrete time index, and $x_k \in \mathbb R^{n_x}$ is now the NARX state vector with
$$
\begin{align}
  x_k = \big[ y_k \ \cdots \ y_{k-m_y} \ u_{k-1} \ \cdots \ u_{k-m_u} \big]^T
\end{align}
$$
that collects the current output, as well as previous outputs and inputs.
We learn the model $f(x_k,u_k)$ from measured input-output data using a Gaussian process.

We are going to train a GP $z = f(w)$ with output $z = y_{k+1}$ and input/regressor $w = (x_k,u_k)$ with $x_k = [y_k, y_{k-1}, y_{k-2}]$.

### Raw data set
We generate a raw data set using the plant equations and different chirp signals on the input.
The data points consist of $(y_{k+1}, y_k, y_{k-1}, y_{k-2}, u_k)$. This data set is later modified to generate training and test data sets for the GP.

In [4]:
# Input sequence composition:
# - 5 small chirps
# - 2 large chirps
chirps = {
    'type': 'linear',
    'amplitude': [6, 6, 6, 6, 6, 18, 18],
    'length': [996, 996, 996, 996, 996, 5 * 996, 5 * 996],
    'mean': [341, 347, 353, 359, 365, 353, 353],
    'chirp_rate': [0.00015, 0.00015, 0.00015, 0.00015, 0.00015, 0.000015, 0.000035]
}
# Standard deviation for noise added to C_A
sigma_n = 5e-3
# Generate data
data_set = plant.generate_data('chirp', shift=2, add_noise={'std': sigma_n, 'seed': 10}, chirps={'T_cr': chirps},
                               skip=('T', 'T_c'))
data_set.plot_raw_data(
    ('t', 'T_cr'),
    ('t', 'C_A_k+1', 'C_A_k', 'C_A_k-1', 'C_A_k-2'),
    title=('input', 'output'),
    figsize=(900, 300),
    layout=(2, 1),
    background_fill_color="#fafafa",
    output_file='gp_nmpc_cstr_output_feedback/raw_data.html',
    output_notebook=True
)

# data_set.add_noise('C_A_k+1', seed=10, std=sigma_n)
data_set.plot_raw_data(
    ('t', 'C_A_k+1_noisy'),
    title="output (noisy)",
    figsize=(900, 300),
    background_fill_color="#fafafa",
    output_file='gp_nmpc_cstr_output_feedback/raw_noisy_data.html',
    output_notebook=True
)

C:\Users\Bruno\Documents\python_packages\examples\lib\site-packages\hilo_mpc\modules\dynamic_model\dynamic_model.py:2939: UserWarning: The model was initialized as a discrete model, but no sampling time was implemented in the model. Assuming that the sampling time 'dt' is already integrated numerically.
  warnings.warn("The model was initialized as a discrete model, but no sampling time was implemented in "



                                                  *#                                                    
                                             %##    %%%                                                 
                                          (%#       %%%%%#                                              
                                         %%     %%%       %%                                            
                                        %%    %%                                                        
                                       %#   %%                                                          
                                     %%%#**%(*%%%%                                                      
                                 %%%****//%#//////%%                                                    
                               %%****/////%/////////%%                                                  
                             %%***///////////////////%

Loading BokehJS ...

Loading BokehJS ...

'gp_nmpc_cstr_output_feedback/raw_noisy_data.html'

### Create training and test data sets
Create the training data set $\mathcal D = \{(z,w)_i\}$ with $z = y_{k+1}$, $w = (x_k,u_k)$ and $x_k = [y_k, y_{k-1}, y_{k-2}]$.
To reduce the number of data points, similar points are removed. For a given data point $(z_i,w_i)$, all following $(z_j,w_j), j > i$ are removed, for which $||w_i - w_j|| < \bar w$ with a chosen threshold $\bar w$.

A test data set for validation is created alongside.


In [5]:
# Training data reduction
data_set.select_train_data('euclidean_distance', distance_threshold=.59)
data_set.plot_train_data(
    ('t', 'T_cr'),
    ('t', 'C_A_k+1_noisy'),
    title=('input', 'output'),
    figsize=(900, 300),
    layout=(2, 1),
    background_fill_color="#fafafa",
    output_file='train_data.html',
    output_notebook=True
)

# Select test data
data_set.select_test_data('downsample', downsample_factor=20)
data_set.plot_test_data(
    ('t', 'T_cr'),
    ('t', 'C_A_k+1_noisy'),
    title=('input', 'output'),
    figsize=(900, 300),
    layout=(2, 1),
    background_fill_color="#fafafa",
    output_file='test_data.html',
    output_notebook=True
)


86/29878 data points selected for training


Loading BokehJS ...

1494/29878 data points selected for testing


Loading BokehJS ...

### Create and train a Gaussian process model
Set up the Gaussian prior distribution and then, based on the training data set $\mathcal D$, generate the posterior distribution (including hyperparameter optimization).


In [6]:
# Initialize the GPs
kernel = SquaredExponentialKernel(active_dims=[1, 2, 3], ard=True)
gp = GP(['x_0', 'x_1', 'x_2', 'u'], ['y'], kernel=kernel, noise_variance=sigma_n ** 2, solver='Newton-CG')
gp.noise_variance.fixed = True

# Training of GP
train_in, train_out = data_set.train_data
gp.set_training_data(train_in, train_out)
gp.setup()
gp.fit_model()

# Validate GP model
test_in, test_out = data_set.test_data
gp.plot_prediction_error(
    test_in,
    test_out,
    figsize=(900, 300),
    layout=(2, 1),
    background_fill_color="#fafafa",
    output_file='gp_prediction_error.html',
    output_notebook=True
)
gp.plot(
    test_in,
    background_fill_color="#fafafa",
    xlabel=('y(k)', 'y(k-1)', 'y(k-2)', 'u(k)'),
    ylabel=4 * ('y(k+1)', ),
    output_file='gp_train_test_scatter.html',
    output_notebook=True
)

Loading BokehJS ...

Loading BokehJS ...

## MPC with GP model
The MPC formulation is
$$
\begin{align}
        \min_{\mathbf{u}_k} \ & \sum_{i=0}^{N-1} \ell \big( \hat x_{k+i|k}, \hat u_{k+i|k}\big) + V_f \big( \hat x_{k+N|k} - x_\text{ref} \big) \ , \\
        \text{s.t.} \quad &\forall i \in \mathcal I_{0:N-1}\!: \\
        & \hat x_{k+i+1|k} = F(\hat x_{k+i|k},\,u_{k+i|k}),\quad \hat x_{k|k}=x_k\\
        & \hat u_{k+i|k} \in \mathcal U \\
        & \hat x_{k+i|k} \in \mathcal X
\end{align}
$$
with the to be optimized input sequence $\mathbf{u}_k = \{u_{k|k}, u_{k+1|k}, \ldots, u_{k+N-1|k}\}$, the prediction horizon $N$, the initial state $x_k$.

As the NARX state is $x_k = [y_k, y_{k-1}, y_{k-2}]$, the NARX state model that we are going to use in the MPC formulation is $\hat x_{k+1} = F(x_k, u_k) = [f(x_k, u_k), y_k, y_{k-1}]$ and the resulting constrained set $\mathcal X = \mathcal Y \times \mathcal Y \times \mathcal Y$.

## GP Prediction Models


In [7]:
gp_model = Model(plot_backend='bokeh', name='GP_Model', discrete=True)

# Set states and inputs
gp_model.set_dynamical_states('x', 3)
gp_model.set_inputs('u', 1)

# States
# x_0(k) := y(k)
# x_1(k) := y(k-1)
# x_2(k) := y(k-2)

# Set difference equations
# x_0(k+1) = y(k+1) = GP
# x_1(k+1) = y(k)   = x_0(k)
# x_2(k+1) = y(k-1) = x_1(k)
gp_model.set_dynamical_equations(['0', 'x_0', 'x_1'])

# Add GP to the ODE's model --> y(k+1) = GP
gp_model += [gp, 0, 0]

# Set up the model
gp_model.setup(dt=Ts)

# Set initial conditions
x0_GP = [y0, y0, y0]
gp_model.set_initial_conditions(x0=x0_GP)

C:\Users\Bruno\Documents\python_packages\examples\lib\site-packages\hilo_mpc\modules\dynamic_model\dynamic_model.py:2939: UserWarning: The model was initialized as a discrete model, but no sampling time was implemented in the model. Assuming that the sampling time 'dt' is already integrated numerically.
  warnings.warn("The model was initialized as a discrete model, but no sampling time was implemented in "


## GP-MPC (model-plant mismatch)

In [8]:
# Build controller
gp_nmpc = NMPC(gp_model)

# Set horizon
gp_nmpc.horizon = 5

# Set cost function
weight_x0 = 10
weight_u = weight_x0 / 15e3
gp_nmpc.quad_stage_cost.add_states(names=['x_0'], weights=[weight_x0], trajectory_tracking=True)
gp_nmpc.quad_stage_cost.add_inputs(names=['u'], weights=[weight_u], trajectory_tracking=True)
gp_nmpc.quad_terminal_cost.add_states(names=['x_0'], weights=[weight_x0], trajectory_tracking=True)

# Set constraints
gp_nmpc.set_box_constraints(x_lb=[y_lb, y_lb, y_lb], x_ub=[y_ub, y_ub, y_ub], u_lb=u_lb, u_ub=u_ub)

# Initial guess
gp_nmpc.set_initial_guess(x_guess=x0_GP, u_guess=u0)

# Set up controller
gp_nmpc.setup(options={'print_level': 1, 'objective_function': 'discrete', 'integration_method': 'discrete'})

# Copy previous solution for comparison
nominal_solution = plant.solution.copy()

# Run the simulation
# NOTE: SimpleControlLoop won't work here, since the model used in the MPC differs too much from the plant model.
#  Maybe in future version an advanced control loop class will be available.
plant.reset_solution()
xk = x0_GP
for _ in range(N_step):
    u = gp_nmpc.optimize(x0=xk, ref_sc={'u': ref_trajectory[1, :], 'x_0': ref_trajectory[0, :]},
                         ref_tc={'x_0': ref_trajectory[0, :]})
    plant.simulate(u=u)
    xk = [plant.solution.get_by_id('x:f')[0], xk[0], xk[1]]  # xk = [y_k, y_{k-1}, y_{k-2}]

C:\Users\Bruno\Documents\python_packages\examples\lib\site-packages\hilo_mpc\modules\base.py:2174: UserWarning: Plots are disabled, since no backend was selected.
  warnings.warn("Plots are disabled, since no backend was selected.")


NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC found an optimal solution.
NMPC fou

## Plots

In [9]:
# Plots
plant.solution.plot(
    ('t', 'T_cr'),
    ('t', 'C_A'),
    data=nominal_solution,
    data_suffix='nominal',
    title=('input', 'output'),
    figsize=(900, 300),
    layout=(2, 1),
    line_width=2,
    background_fill_color='#fafafa',
    output_file='gp_nmpc_cstr_output_feedback/gp_mpc_vs_nominal_mpc.html',
    output_notebook=True
)

Loading BokehJS ...

'gp_nmpc_cstr_output_feedback/gp_mpc_vs_nominal_mpc.html'